In [190]:
import networkx as nx
from random import random, choice

In [10]:

def label_BFS(s,K,K_s,T,r,t,a,ext):

    def label_extension(l,arc,dominated):
        for m in range(1):
            i = arc[0]; j = arc[1]
            new_label = [[], 0, 0, 0]

            ''' Check cycle feasibility '''
            if j in l[0]: break

            ''' Check waiting line feasibility '''
            if a[j,s] < l[2]: break
            if a[j,s] > l[3]: new_label[2] = l[2]
            else: new_label[2] = l[3]

            ''' Check time consumption feasibility '''
            if l[3] > a[j,s] + T: break
            new_label[3] = l[3] + max(0,a[j,s]-l[3]) + t[j,s]
            
            ''' Update the resources consumption '''
            new_label[0] += l[0] + [j]
            new_label[1] = l[1] + r[(i,j)]
            
            if j == "e" and new_label[1] < -0.001:
                done.append(new_label)
            else:
                new_labels[j].append(new_label)
                label_dominance(new_label,j,dominated)
    
    def label_dominance(new_label,j,dominated):
        for l in range(len(labels[j])):
            if set(labels[j][l][0]).issubset(set(new_label[0])):
                dominated[j][l] = True

    ''' Labels list '''
    # Index: number of label
    # 0: route
    # 1: cumulative reduced cost
    # 2: last moment where there was a vehicle waiting in line to use the charger
    # 3: cumulative time consumption
    labels = dict()
    for k in K_s:
        if ("s",k) in ext["s"]: labels[k] = [ [["s",k], r["s",k], a[k,s], a[k,s]+t[k,s]] ]
        else: labels[k] = []
    done = []

    act = 1
    while act > 0:
        
        L = {k:len(labels[k]) for k in K_s}
        new_labels = {k:[] for k in K_s}
        dominated = {k:{l:False for l in range(L[k])} for k in K_s}
        for k in K_s:
            for l in range(L[k]):
                if not dominated[k][l]:
                    for arc in ext[labels[k][l][0][-1]]:
                        label_extension(labels[k][l], arc, dominated)

        labels = new_labels.copy()
        act = sum(len(labels[k]) for k in K_s)
    

    return done

def vertices_extensions(V,A):
    
    G = nx.DiGraph()
    G.add_nodes_from(V); G.add_edges_from(A)
    outbound_arcs = {}
    for v in V:
        outbound_arcs[v] = list(G.out_edges(v))
    
    return outbound_arcs

def get_graph(s,K,a,pi,sigma):

    dist = {k:a[k,s] for k in K if pi[k]>0}
    Ks = [k for k in sorted(dist, key=dist.get)]

    V = ["s"] + Ks + ["e"]
    A = [(i,j) for i in V for j in V if i!=j and i!="e" and j!="s" and a[i,s] <= a[j,s] and (i,j)!=("s","e")]

    rc = {arc:-pi[arc[1]]-sigma if arc[0]=="s" else (0 if arc[1]=="e" else -pi[arc[1]]) for arc in A}
    
    return V,A,rc

In [183]:
def label_DFS(v,rP,tP,qP,P,cK,L,s,r,t,a,T,ext):
    for m in range(1):
        ''' Check feasibility '''
        #if (set(P).issubset(cK) and len(P)<len(cK) and P!=["s"]) or v in P or v in cK: print(f"\tinfeasible, cycle. P:{P} cK:{cK}"); break
        if len(cK) > 0 and (P[-1] in cK or (P[-1]=="s" and v in cK)): break#; print(f"\tInfeasible, already covered. P:{P[1:]}, cK:{cK}")
        
        if v in P: break
        if a[v,s] < qP: break
        if tP - t[v,s] > a[v,s] + T: break

        nP = P + [v]
        if v == "e": L.append(P[1:]); cK.update(nP[1:-1])#; print(f"\t***NEW PATH FOUND***: P:{P[1:]}   cK:{cK}")

        if a[v,s] == tP - t[v,s]: nqP = qP
        else: nqP = tP - t[v,s]

        for arc in ext[v]:
            vv = arc[1]
            ntP = max(tP,a[vv,s]) + t[vv,s]
            nrP = rP + r[v,vv]
            #print(f"Trying for subpath {nP} + {vv}")
            label_DFS(vv,nrP,ntP,nqP,nP,cK,L,s,r,t,a,T,ext)



In [197]:
K = list(range(1,51))
T = 4
a = {(k,1):0.5+random()*2+2*choice([0,1,2]) for k in K}
t = {(k,1):0.3+random()*2.5 for k in K}
a.update({("s",1):0,("e",1):15})
t.update({("s",1):0,("e",1):0})
V,A,rc = get_graph(1,K,a,{k:10 for k in K},0)
ext = vertices_extensions(V,A)

In [11]:
cd = 0.041
cw = 0.0388

K = list(range(1,5))
T = 4
a = {("s",1):0, (1,1):10/60, (2,1):30/60, (3,1):40/60, (4,1):80/60, ("e",1):15}
t = {("s",1):0, (1,1):40/60, (2,1):30/60, (3,1):30/60, (4,1):20/60, ("e",1):0}
V,A,rc = get_graph(1,K,a,{k:10 for k in K},0)
ext = vertices_extensions(V,A)




In [198]:
routes_BFS = label_BFS(1,K,K,T,rc,t,a,ext)
for l in routes_BFS:
    print(l[0])

['s', 1, 'e']
['s', 2, 'e']
['s', 3, 'e']
['s', 16, 'e']
['s', 22, 'e']
['s', 34, 'e']
['s', 2, 1, 'e']
['s', 3, 1, 'e']
['s', 16, 1, 'e']
['s', 22, 1, 'e']
['s', 34, 1, 'e']
['s', 3, 2, 'e']
['s', 16, 2, 'e']
['s', 22, 2, 'e']
['s', 34, 2, 'e']
['s', 16, 3, 'e']
['s', 22, 3, 'e']
['s', 34, 3, 'e']
['s', 22, 4, 'e']
['s', 22, 10, 'e']
['s', 22, 11, 'e']
['s', 22, 12, 'e']
['s', 34, 12, 'e']
['s', 22, 13, 'e']
['s', 22, 16, 'e']
['s', 34, 16, 'e']
['s', 22, 18, 'e']
['s', 34, 22, 'e']
['s', 34, 46, 'e']
['s', 22, 48, 'e']
['s', 34, 48, 'e']
['s', 16, 2, 1, 'e']
['s', 34, 2, 1, 'e']
['s', 16, 3, 1, 'e']
['s', 34, 3, 1, 'e']
['s', 34, 12, 1, 'e']
['s', 34, 16, 1, 'e']
['s', 34, 22, 1, 'e']
['s', 34, 46, 1, 'e']
['s', 34, 48, 1, 'e']
['s', 16, 3, 2, 'e']
['s', 34, 3, 2, 'e']
['s', 34, 12, 2, 'e']
['s', 34, 16, 2, 'e']
['s', 34, 22, 2, 'e']
['s', 34, 46, 2, 'e']
['s', 34, 48, 2, 'e']
['s', 16, 1, 4, 'e']
['s', 16, 2, 4, 'e']
['s', 16, 3, 4, 'e']
['s', 34, 3, 4, 'e']
['s', 34, 12, 4, 'e']
['

In [199]:
routes_DFS = []
covered_nodes = set()
label_DFS(v="s",rP=0,tP=0,qP=0,P=[],cK=covered_nodes,L=routes_DFS,s=1,r=rc,t=t,a=a,T=T,ext=ext)

In [200]:
routes_DFS

[[34, 46, 2, 1, 6, 36, 43],
 [22, 16, 44, 15, 35],
 [3, 12, 33, 8, 21],
 [48, 13, 10, 27, 31, 24, 37],
 [32, 38, 29, 19],
 [28, 23, 50, 14],
 [11, 47, 41, 20],
 [26, 4, 30, 25, 42],
 [49, 18, 7],
 [40, 9],
 [45, 17],
 [5, 39]]

In [196]:
V

['s',
 47,
 8,
 7,
 39,
 24,
 6,
 29,
 9,
 45,
 46,
 26,
 12,
 49,
 32,
 14,
 17,
 18,
 10,
 41,
 33,
 3,
 40,
 36,
 28,
 22,
 23,
 25,
 31,
 16,
 4,
 38,
 5,
 19,
 35,
 42,
 27,
 44,
 50,
 21,
 11,
 43,
 15,
 30,
 1,
 2,
 20,
 37,
 13,
 34,
 48,
 'e']

In [110]:
li = [0]
li[1]

IndexError: list index out of range